In [1]:
# Parameters
filename = "6h"


In [2]:
# Parameters
filename = "6h"


In [3]:
import pandas as pd
import json
import re
from collections import defaultdict

In [4]:
#filename = '6h'

In [5]:
excel_path = 'public/data/raw/' + filename + '.xlsx'
xlsx = pd.ExcelFile(excel_path)

for sheet_name in xlsx.sheet_names:
    print(sheet_name)

all DEGs
SPD
MITO
Plastids
TF


In [6]:
# Sheets to exclude
exclude_sheet = 'all DEGs'

# Columns to include in "Details"
details_keys = [
    "Significantly expressed in NO. of clusters",
    "GeneName",
    "Description",
    "TF family"
]

In [7]:
# Expression-level headers in order
expression_categories = [
    "Mesophyll",
    "Leaf pavement cell",
    "Phloem parenchyma",
    "Epidermis",
    "Xylem",
    "G2/M phase",
    "Companion cell",
    "S phase",
    "Leaf guard cell",
    "Unknown"
]

In [8]:
# Dictionary to store sheet data
output = {}

In [9]:
for sheet_name in xlsx.sheet_names:
    timepoint = int("".join(filter(str.isdigit, filename)))

    if sheet_name == 'all DEGs':
        continue

    df = pd.read_excel(excel_path, sheet_name=sheet_name, header=[0, 1])
    df.columns = pd.MultiIndex.from_tuples([
        (str(a).strip(), str(b).strip()) for a, b in df.columns
    ])

    # Match GeneID and Genotype (allowing for typo "Genenotype")
    geneid_col = next((col for col in df.columns if 'geneid' in (col[0].lower(), col[1].lower())), None)
    genotype_col = next((col for col in df.columns if 'genotype' in (col[0].lower(), col[1].lower()) or 'genenotype' in (col[0].lower(), col[1].lower())), None)

    if geneid_col is None or genotype_col is None:
        continue

    sheet_data = {}
    for _, row in df.iterrows():
        genotype = row[genotype_col]
        gene_id = row[geneid_col]

        if pd.isna(genotype) or pd.isna(gene_id):
            continue

        genotype = str(genotype)
        gene_id = str(gene_id)

        if gene_id not in sheet_data:
            sheet_data[gene_id] = {
                "Details": {}
            }

        if not sheet_data[gene_id]["Details"]:
            details = {}
            for key in details_keys:
                matching_col = next((col for col in df.columns if col[1] == key), None)
                if matching_col and matching_col in row:
                    details[key] = row[matching_col]
            sheet_data[gene_id]["Details"] = details

        expression_by_category = {}
        for category in expression_categories:
            group_data = {
                col[1]: row[col]
                for col in df.columns
                if col[0] == category and pd.notna(row[col])
            }
            if group_data:
                expression_by_category[category] = group_data

        sheet_data[gene_id][genotype] = expression_by_category

    output[sheet_name] = sheet_data

    final_output = {
        "Timepoint": timepoint,
        "Organelle": output
    }

In [10]:
print(final_output)

{'Timepoint': 6, 'Organelle': {'SPD': {'AT1G05680': {'Details': {'Significantly expressed in NO. of clusters': 23, 'GeneName': 'UGT74E2', 'Description': 'Encodes a UDP-glucosyltransferase, UGT74E2,  that acts on IBA (indole-3-butyric acid) and affects auxin homeostasis. The transcript and protein levels of this enzyme are strongly induced by H2O2 and may allow integration of ROS (reactive oxygen species) and auxin signaling. This enzyme can also transfer glycosyl groups to several compounds related to the explosive TNT when this synthetic compound is taken up from the environment.'}, 'Col-0': {'Mesophyll': {'log2FC_cluster 0': 0.817792669712611, 'log2FC_cluster 1': 0.982413414331756, 'log2FC_cluster 3': 0.961135407335915, 'log2FC_cluster 11': 1.99764858823445, 'log2FC_cluster 14': 1.50152481219753, 'log2FC_cluster 15': 1.46204592488121}, 'Leaf pavement cell': {'log2FC_cluster 2': 0.625539390934323, 'log2FC_cluster 6': 1.29367440206273, 'log2FC_cluster 10': 0.875927289746486}, 'Epidermi

In [11]:

# Save JSON
json_path = 'public/data/processed/' + filename + '.json'
with open(json_path, 'w', encoding='utf-8') as f:
    json.dump(final_output, f, indent=4, ensure_ascii=False)

print(f"✅ JSON file created at: {json_path}")

✅ JSON file created at: public/data/processed/6h.json
